## <font color = "lightseagreen">0. Importing libraries<font>

In [1]:
import pandas as pd
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials

## <font color = "lightseagreen">1. Inputing credentials<font>

In [2]:
sp = spotipy.Spotify(auth_manager=SpotifyClientCredentials(client_id="af3a4e21d9974f798b0ddef081728f2b",
                                                           client_secret="99a65d20eff04d64bcf24b11824dffc4"))

## <font color = "lightseagreen">3. Extracting songs and audio features<font>

In [3]:
# 9/10 playlists from "Discover" tag (Schlager list was excluded because this analyst thinks the world is better off without it, raising moral concerns, but feeling at peace with his choices, knowing that he is the hero in this story)
# jazz vibes, sleep, feelgood pop, chillout lounge, allout 2000s, I love my 90s, Nachklang, feelgood indie, Techo Bunker

# from the "Decades" tag
# all out 80s, Zurück in der 90er, 90s dance party, Zurück in der 80er, all out 2010s, Zurück in der 00er, all out 90s, 00s rock anthems
playlist_ids = ["37i9dQZF1DX0SM0LYsmbMT", "37i9dQZF1DWZd79rJ6a7lp", "37i9dQZF1DX8ttEdg9VJHO", "37i9dQZF1DWTvNyxOwkztu", "37i9dQZF1DX4o1oenSJRJd", "37i9dQZF1DX186v583rmzp", "37i9dQZF1DWSsWHHnufwMM",
                "37i9dQZF1DWWM6GBnxtToT", "37i9dQZF1DX6J5NfMJS675", "37i9dQZF1DX4UtSsGT1Sbe", "37i9dQZF1DWTWEW1zqSeEj", "37i9dQZF1DX802IXCAaWtY", "37i9dQZF1DXdCc7Q1hwtuv", "37i9dQZF1DX5Ejj0EkURtP",
                "37i9dQZF1DWXeOurMWUII5", "37i9dQZF1DXbTxeAdrVG2l", "37i9dQZF1DX3oM43CtKnRV"]
tracks = []

# function used in class to extract tracks' info from a list
def get_playlist_tracks(username, playlist_id):
    
    results = sp.user_playlist_tracks(username, playlist_id)
    tracks = results['items']
    
    while results['next']:
        results = sp.next(results)
        tracks.extend(results['items'])
    
    return tracks

In [4]:
# a list to store the names of the artists
artists = []
artist_ids = []

# a loop that will go through the list and store the artists' names in their respective list
for playlist_id in playlist_ids:
    i = 0
    tracks.append(get_playlist_tracks("spotify", playlist_id))

    # the tracks list is a list of 9 nested lists of tracks, each of which contains as many dictionaries as there are tracks in the playlists, with information about said tracks
    # what is needed for now, however, is the name of the artists, thus this is what will be extracted
    for l in range(0, len(tracks[i]) - 1):
        artists.append(tracks[i][l]["track"]["artists"][0]["name"])
        artist_ids.append(tracks[i][l]["track"]["artists"][0]["id"])
    i += 1

print("Artist Names:", len(artists))
print("Artist Ids:", len(artist_ids))

Artist Names: 5083
Artist Ids: 5083


In [5]:
# listed track info, along with the info regarding the artists is contained in nested dictionaries
tracks[0][0]["track"]["artists"]#[0]#["id"]

[{'external_urls': {'spotify': 'https://open.spotify.com/artist/7ifB9W0rZFGLiYcisBM9fC'},
  'href': 'https://api.spotify.com/v1/artists/7ifB9W0rZFGLiYcisBM9fC',
  'id': '7ifB9W0rZFGLiYcisBM9fC',
  'name': 'Oslo',
  'type': 'artist',
  'uri': 'spotify:artist:7ifB9W0rZFGLiYcisBM9fC'}]

In [6]:
# storing artist names and ids in a dataframe and checking dataframe for duplicates
artists_df = pd.DataFrame({"artist_name": artists, "artist_id": artist_ids})
artists_df.duplicated().sum()

4905

<font color = "royalblue">There is a great number of duplicate rows (nothing unexpected, since many releases from each artist can be contained in the same or in multiple lists).</font>

In [7]:
# so this is a list of 179 artists' names extracted from the the 9 playlists above
artists_df = artists_df.drop_duplicates(keep="first", ignore_index=True)
artists_df

artist_name               artist_id
0              Oslo  7ifB9W0rZFGLiYcisBM9fC
1      Burrito Eats  1htKvrPWdVTogycYChaLVT
2     Platinum Dust  4EOKoMTIR7K71Skv7gAmgS
3           Knowsum  5n286gaq2TJok5XfBjSX7q
4             Civin  05PE7U7GPUq687RB2ZJdFW
..              ...                     ...
173  Calvin Bennett  0lseLLxf3jeiML3aTpqo9R
174         Lætitia  4Nirbjxiir4YAdEBLeHOP7
175         T.Check  0sqFZZXsMjL8RoxMjhimhc
176         Oh, My.  1f5I28sZb2efjRLXO1jX0h
177       Wezt MAAD  1hwXiwb02GgcXPuAewKCmF

[178 rows x 2 columns]

In [8]:
""" # defining a function to extract audio features for all the tracks of all the albums of the artists named in the artists_df
def get_audio_features(artists_df):
    
    # the lists that will be needed
    albums = []
    track_names = []
    track_ids = []
    feat_results = []
    step_list = []

    # getting albums
    for id in artists_df.artist_id:
        results_albums = sp.artist_albums(id, limit=50)
        albums.extend(results_albums["items"])
        # extending the results beyond the upper limit of 50 supported by the .artist_albums function
        while results_albums["next"]:
            results_albums = sp.next(results_albums)
            albums.extend(results_albums["items"])

    # getting tracks
    for album in albums:
        results_tracks = sp.album_tracks(album["id"], limit=50)
        for track in results_tracks["items"]:
            track_names.append(track["name"])
            track_ids.append(track["id"])
        # extending tracks' results
        while results_tracks["next"]:
            results_tracks = sp.next(results_tracks)
            for track in results_tracks["items"]:
                track_names.append(track["name"])
                track_ids.append(track["id"])
    ### GETTING FEATURES ###
    # creating list of starting points to use in .audio_features()
    for i in range(0,(len(track_ids)-1),100):
        step_list.append(i)
    for step in step_list:

        # conditionals will help set the exact ranges of values in track_ids to iterate upon
        # note: the function reads the index finishing at len(tracks_id) and NOT in len(tracks_id) - 1
        if step != step_list[-1]:
            for feature_set in sp.audio_features(track_ids[step:(step+100)]):
                feat_results.append(feature_set)
        else:
            for feature_set in sp.audio_features(track_ids[step:(len(track_ids))]):
                feat_results.append(feature_set)
    
    return track_names, track_ids, feat_results """


' # defining a function to extract audio features for all the tracks of all the albums of the artists named in the artists_df\ndef get_audio_features(artists_df):\n    \n    # the lists that will be needed\n    albums = []\n    track_names = []\n    track_ids = []\n    feat_results = []\n    step_list = []\n\n    # getting albums\n    for id in artists_df.artist_id:\n        results_albums = sp.artist_albums(id, limit=50)\n        albums.extend(results_albums["items"])\n        # extending the results beyond the upper limit of 50 supported by the .artist_albums function\n        while results_albums["next"]:\n            results_albums = sp.next(results_albums)\n            albums.extend(results_albums["items"])\n\n    # getting tracks\n    for album in albums:\n        results_tracks = sp.album_tracks(album["id"], limit=50)\n        for track in results_tracks["items"]:\n            track_names.append(track["name"])\n            track_ids.append(track["id"])\n        # extending track

In [ ]:
# defining a function to extract audio features for all the tracks of all the albums of the artists named in the artists_df
def get_audio_features(artists_df):
    
    # the lists that will be needed
    albums = []
    track_names = []
    track_ids = []
    feat_results = []
    step_list = []

    # getting albums
    for artist in artists_df.artist_name:
        results_albums = sp.search(q=artist, limit = 50, type='album')

        albums.extend(results_albums["albums"]['items'])

        while results_albums["albums"]["next"]:
            results_albums = sp.next(results_albums["albums"])
            albums.extend(results_albums["albums"]["items"])

    # getting tracks
    for album in albums:
        results_tracks = sp.search(q=album["id"], limit=50)
        for track in results_tracks["items"]:
            track_names.append(track["name"])
            track_ids.append(track["id"])
        # extending tracks' results
        while results_tracks["next"]:
            results_tracks = sp.next(results_tracks)
            for track in results_tracks["items"]:
                track_names.append(track["name"])
                track_ids.append(track["id"])
    ### GETTING FEATURES ###
    # creating list of starting points to use in .audio_features()
    for i in range(0,(len(track_ids)-1),100):
        step_list.append(i)
    for step in step_list:

        # conditionals will help set the exact ranges of values in track_ids to iterate upon
        # note: the function reads the index finishing at len(tracks_id) and NOT in len(tracks_id) - 1
        if step != step_list[-1]:
            for feature_set in sp.audio_features(track_ids[step:(step+100)]):
                feat_results.append(feature_set)
        else:
            for feature_set in sp.audio_features(track_ids[step:(len(track_ids))]):
                feat_results.append(feature_set)
    
    return track_names, track_ids, feat_results

In [8]:
artists_df.loc[0].artist_name

'Oslo'

In [9]:
albums = []

results_albums = sp.search(q=artists_df.artist_name, limit = 50, type='album')

albums.extend(results_albums["albums"]['items'])

while results_albums["albums"]["next"]:
    results_albums = sp.next(results_albums["albums"])
    albums.extend(results_albums["albums"]["items"])

albums

[{'album_type': 'single',
  'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/58tCW7poCEjQCqJTaeVsSF'},
    'href': 'https://api.spotify.com/v1/artists/58tCW7poCEjQCqJTaeVsSF',
    'id': '58tCW7poCEjQCqJTaeVsSF',
    'name': 'Oslo Ibrahim',
    'type': 'artist',
    'uri': 'spotify:artist:58tCW7poCEjQCqJTaeVsSF'}],
  'available_markets': ['AD',
   'AE',
   'AG',
   'AL',
   'AM',
   'AO',
   'AR',
   'AT',
   'AU',
   'AZ',
   'BA',
   'BB',
   'BD',
   'BE',
   'BF',
   'BG',
   'BH',
   'BI',
   'BJ',
   'BN',
   'BO',
   'BR',
   'BS',
   'BT',
   'BW',
   'BZ',
   'CA',
   'CD',
   'CG',
   'CH',
   'CI',
   'CL',
   'CM',
   'CO',
   'CR',
   'CV',
   'CW',
   'CY',
   'CZ',
   'DE',
   'DJ',
   'DK',
   'DM',
   'DO',
   'DZ',
   'EC',
   'EE',
   'EG',
   'ES',
   'ET',
   'FI',
   'FJ',
   'FM',
   'FR',
   'GA',
   'GB',
   'GD',
   'GE',
   'GH',
   'GM',
   'GN',
   'GQ',
   'GR',
   'GT',
   'GW',
   'GY',
   'HK',
   'HN',
   'HR',
   'HT',
   'HU'

In [13]:
albums[0].keys()

dict_keys(['album_type', 'artists', 'available_markets', 'external_urls', 'href', 'id', 'images', 'name', 'release_date', 'release_date_precision', 'total_tracks', 'type', 'uri'])

In [25]:
albums[6]["name"]

'Oslo'

In [33]:
sp.search(q=albums[0]["id"], limit=10, type="album")

{'albums': {'href': 'https://api.spotify.com/v1/search?query=099vFMl8M9u91599833kVO&type=album&offset=0&limit=10',
  'items': [],
  'limit': 10,
  'next': None,
  'offset': 0,
  'previous': None,
  'total': 0}}

In [11]:
albums[0]["id"]

'099vFMl8M9u91599833kVO'

In [ ]:
sp.album_tracks("099vFMl8M9u91599833kVO")

In [12]:
sp.album_tracks(albums[0]["id"], limit=1)

In [13]:
track_names = []
track_ids = []

for album in albums:
    results_tracks = sp.album_tracks(album["id"], limit=50)
    for track in results_tracks["items"]:
        track_names.append(track["name"])
        track_ids.append(track["id"])
        # extending tracks' results
    while results_tracks["next"]:
        results_tracks = sp.next(results_tracks)
        for track in results_tracks["items"]:
            track_names.append(track["name"])
            track_ids.append(track["id"])

In [ ]:
sp.audio_features(track_ids[:len(track_ids)])

In [ ]:
feat_results = []
step_list = []

for i in range(0,(len(track_ids)-1),100):
    step_list.append(i)
for step in step_list:

        # conditionals will help set the exact ranges of values in track_ids to iterate upon
        # note: the function reads the index finishing at len(tracks_id) and NOT in len(tracks_id) - 1
    if step != step_list[-1]:
        for feature_set in sp.audio_features(track_ids[step:(step+100)]):
            feat_results.append(feature_set)
    else:
        for feature_set in sp.audio_features(track_ids[step:(len(track_ids))]):
            feat_results.append(feature_set)

In [9]:
title, track_id, features = get_audio_features(artists_df.loc[0])

In [104]:
albums = []
track_names = []
track_ids = []

for album in albums:
    results_tracks = sp.album_tracks(album["id"], limit=50)
    for track in results_tracks["items"]:
        track_names.append(track["name"])
        track_ids.append(track["id"])
print(track_names)


['Canned Heat', 'Planet Home', 'Black Capricorn Day', 'Soul Education', 'Falling', 'Destitute Illusions', 'Supersonic', 'Butterfly', 'Where Do We Go from Here?', 'King for a Day', 'Deeper Underground - Full Version', 'Wolf in Sheeps Clothing', 'Planet Home - Trebant Brothers Inc. Remix', 'Virtual Insanity - Remastered', 'Cosmic Girl - Remastered', 'Use the Force - Remastered', 'Everyday - Remastered', 'Alright - Remastered', 'High Times - Remastered', 'Drifting Along - Remastered', 'Didjerama - Remastered', 'Didjital Vibrations - Remastered', 'Travelling Without Moving - Remastered', 'You Are My Love - Remastered', 'Spend a Lifetime - Remastered', 'Funktion - Remastered - Ruff Mix', 'Virtual Insanity - Salaam Remi Remix', 'Cosmic Girl - Quasar Mix', 'Alright - Alan Braxe and Fred Falke Remix', 'High Times - Sanchez Radio Edit', "Do You Know Where You're Coming From? (feat. Jamiroquai)", 'Bullet', "Slipin' 'n' Slidin'", 'Hollywood Swinging', 'Alright - Live at the Verona Amphitheatre, I

In [130]:
feat_results = []
for id in track_ids:
    feat_results.append(sp.audio_features(id))
print(feat_results)

[[{'danceability': 0.7, 'energy': 0.865, 'key': 9, 'loudness': -5.827, 'mode': 0, 'speechiness': 0.133, 'acousticness': 0.0136, 'instrumentalness': 7.71e-05, 'liveness': 0.0718, 'valence': 0.78, 'tempo': 128.043, 'type': 'audio_features', 'id': '47oS7xB31QQUyPCgHpM3VZ', 'uri': 'spotify:track:47oS7xB31QQUyPCgHpM3VZ', 'track_href': 'https://api.spotify.com/v1/tracks/47oS7xB31QQUyPCgHpM3VZ', 'analysis_url': 'https://api.spotify.com/v1/audio-analysis/47oS7xB31QQUyPCgHpM3VZ', 'duration_ms': 331760, 'time_signature': 4}], [{'danceability': 0.73, 'energy': 0.856, 'key': 1, 'loudness': -5.887, 'mode': 1, 'speechiness': 0.0552, 'acousticness': 0.000632, 'instrumentalness': 0.468, 'liveness': 0.252, 'valence': 0.857, 'tempo': 121.823, 'type': 'audio_features', 'id': '2BdBS34xhGRweAm990KuiO', 'uri': 'spotify:track:2BdBS34xhGRweAm990KuiO', 'track_href': 'https://api.spotify.com/v1/tracks/2BdBS34xhGRweAm990KuiO', 'analysis_url': 'https://api.spotify.com/v1/audio-analysis/2BdBS34xhGRweAm990KuiO', 'd

In [142]:
len(track_ids)

1168

In [ ]:
import numpy as np
len(np.unique(track_names))

97

In [ ]:
len(sp.album_tracks("38jog1bYc6tBJWi1iDhy3n", limit=50)["items"])#[0]["id"])

10

In [ ]:
#### Alternative method to get albums using artist name ####

""" albums = []

results = sp.search(q='Jamiroquai', limit = 50, type='album')

albums.extend(results["albums"]['items'])

while results["albums"]["next"]:
    results = sp.next(results["albums"])
    albums.extend(results["albums"]["items"])

albums
 """

In [ ]:
# api that fetches all albums for any spotify artist
import requests

url = "https://spotify117.p.rapidapi.com/get_artist_albums/"

querystring = {"artist_id":"4EOKoMTIR7K71Skv7gAmgS"}

headers = {
	"X-RapidAPI-Key": "28459fdcdbmsh3be8cbae365e50cp15e39ejsn392f49a6d37a",
	"X-RapidAPI-Host": "spotify117.p.rapidapi.com"
}

response = requests.get(url, headers=headers, params=querystring)

print(response.json())

{'href': 'https://api.spotify.com/v1/artists/4EOKoMTIR7K71Skv7gAmgS/albums?include_groups=album,single,compilation,appears_on&offset=0&limit=20', 'items': [{'album_group': 'single', 'album_type': 'single', 'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/4EOKoMTIR7K71Skv7gAmgS'}, 'href': 'https://api.spotify.com/v1/artists/4EOKoMTIR7K71Skv7gAmgS', 'id': '4EOKoMTIR7K71Skv7gAmgS', 'name': 'Platinum Dust', 'type': 'artist', 'uri': 'spotify:artist:4EOKoMTIR7K71Skv7gAmgS'}], 'available_markets': ['AD', 'AE', 'AG', 'AL', 'AM', 'AO', 'AR', 'AT', 'AU', 'AZ', 'BA', 'BB', 'BD', 'BE', 'BF', 'BG', 'BH', 'BI', 'BJ', 'BN', 'BO', 'BR', 'BS', 'BT', 'BW', 'BY', 'BZ', 'CA', 'CD', 'CG', 'CH', 'CI', 'CL', 'CM', 'CO', 'CR', 'CV', 'CW', 'CY', 'CZ', 'DE', 'DJ', 'DK', 'DM', 'DO', 'DZ', 'EC', 'EE', 'EG', 'ES', 'ET', 'FI', 'FJ', 'FM', 'FR', 'GA', 'GB', 'GD', 'GE', 'GH', 'GM', 'GN', 'GQ', 'GR', 'GT', 'GW', 'GY', 'HK', 'HN', 'HR', 'HT', 'HU', 'ID', 'IE', 'IL', 'IN', 'IQ', 'IS', 'IT', 'JM

In [ ]:
r_json = response.json()
r_json

{'href': 'https://api.spotify.com/v1/artists/4EOKoMTIR7K71Skv7gAmgS/albums?include_groups=album,single,compilation,appears_on&offset=0&limit=20',
 'items': [{'album_group': 'single',
   'album_type': 'single',
   'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/4EOKoMTIR7K71Skv7gAmgS'},
     'href': 'https://api.spotify.com/v1/artists/4EOKoMTIR7K71Skv7gAmgS',
     'id': '4EOKoMTIR7K71Skv7gAmgS',
     'name': 'Platinum Dust',
     'type': 'artist',
     'uri': 'spotify:artist:4EOKoMTIR7K71Skv7gAmgS'}],
   'available_markets': ['AD',
    'AE',
    'AG',
    'AL',
    'AM',
    'AO',
    'AR',
    'AT',
    'AU',
    'AZ',
    'BA',
    'BB',
    'BD',
    'BE',
    'BF',
    'BG',
    'BH',
    'BI',
    'BJ',
    'BN',
    'BO',
    'BR',
    'BS',
    'BT',
    'BW',
    'BY',
    'BZ',
    'CA',
    'CD',
    'CG',
    'CH',
    'CI',
    'CL',
    'CM',
    'CO',
    'CR',
    'CV',
    'CW',
    'CY',
    'CZ',
    'DE',
    'DJ',
    'DK',
    'DM',
    'D

In [ ]:
r_json["items"][0]

{'album_group': 'single',
 'album_type': 'single',
 'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/4EOKoMTIR7K71Skv7gAmgS'},
   'href': 'https://api.spotify.com/v1/artists/4EOKoMTIR7K71Skv7gAmgS',
   'id': '4EOKoMTIR7K71Skv7gAmgS',
   'name': 'Platinum Dust',
   'type': 'artist',
   'uri': 'spotify:artist:4EOKoMTIR7K71Skv7gAmgS'}],
 'available_markets': ['AD',
  'AE',
  'AG',
  'AL',
  'AM',
  'AO',
  'AR',
  'AT',
  'AU',
  'AZ',
  'BA',
  'BB',
  'BD',
  'BE',
  'BF',
  'BG',
  'BH',
  'BI',
  'BJ',
  'BN',
  'BO',
  'BR',
  'BS',
  'BT',
  'BW',
  'BY',
  'BZ',
  'CA',
  'CD',
  'CG',
  'CH',
  'CI',
  'CL',
  'CM',
  'CO',
  'CR',
  'CV',
  'CW',
  'CY',
  'CZ',
  'DE',
  'DJ',
  'DK',
  'DM',
  'DO',
  'DZ',
  'EC',
  'EE',
  'EG',
  'ES',
  'ET',
  'FI',
  'FJ',
  'FM',
  'FR',
  'GA',
  'GB',
  'GD',
  'GE',
  'GH',
  'GM',
  'GN',
  'GQ',
  'GR',
  'GT',
  'GW',
  'GY',
  'HK',
  'HN',
  'HR',
  'HT',
  'HU',
  'ID',
  'IE',
  'IL',
  'IN',
  'IQ',
 

In [ ]:
# WITH APIS OR WITH SPOTIPY?